In [1]:
import numpy as np
import phate
import sys
sys.path.append('../../src/')
from data_script import hemisphere_data, sklearn_swiss_roll
from data_convert import convert_data
from plotly3d.plot import scatter
from negative_sampling import add_negative_samples, make_hi_freq_noise
import pathlib
from scipy.spatial.distance import pdist, squareform
from sklearn.model_selection import train_test_split
import phate
import numpy as np
from scipy.spatial.distance import pdist, squareform
from omegaconf import DictConfig, OmegaConf
import hydra

Generate data

In [2]:
gt_X, X, _ = sklearn_swiss_roll(n_samples=1000, noise=0.0)

In [3]:
x = X
x2 = x.copy()
x2[:,1] = x[:,1] + x[:,1].max()
x3 = np.r_[x,x2]
x2 = x3.copy()
x2[:,1] = x3[:,1] + x3[:,1].max()
x3 = np.r_[x3,x2]
X = x3

In [21]:
def convert_data(X, seed=42, test_size=0.2, knn=5, t=30, n_components=3, decay=40):
    # phate_op = phate.PHATE(random_state=42, knn=20, t=30, n_components=3, decay=5)
    phate_op = phate.PHATE(random_state=seed, t=t, n_components=n_components, knn=knn, decay=decay)
    phate_data = phate_op.fit_transform(X)
    colors = np.zeros(X.shape[0])
    dists_all = squareform(pdist(phate_op.diff_potential))
    ids = np.arange(0, X.shape[0])
    id_train, id_test = train_test_split(ids, test_size=test_size, random_state=seed)
    is_train = np.isin(ids, id_train)
    X_train = X[is_train]
    # phate_op = phate.PHATE(random_state=seed, knn=20, t=30, n_components=3, decay=5)
    phate_op = phate.PHATE(random_state=seed, t=t, n_components=n_components, knn=knn, decay=decay)
    _ = phate_op.fit_transform(X_train)
    dists = dists_all.copy()
    dists_train = squareform(pdist(phate_op.diff_potential))
    dists[is_train][:,is_train] = dists_train
    return dict(
        data=X,
        colors=colors,
        dist=dists,
        dist_all=dists_all, # deprecated.
        phate=phate_data,
        is_train=is_train
    )

In [14]:
data_dict0 = convert_data(X, knn=5, t=30)

Calculating PHATE...
  Running PHATE on 4000 observations and 3 variables.
  Calculating graph and diffusion operator...
    Calculating KNN search...
    Calculated KNN search in 0.04 seconds.
    Calculating affinities...
    Calculated affinities in 0.02 seconds.
  Calculated graph and diffusion operator in 0.07 seconds.
  Calculating landmark operator...
    Calculating SVD...
    Calculated SVD in 0.19 seconds.
    Calculating KMeans...
    Calculated KMeans in 3.90 seconds.
  Calculated landmark operator in 5.12 seconds.
  Calculating diffusion potential...
  Calculated diffusion potential in 1.49 seconds.
  Calculating metric MDS...


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/sklearn/manifold/_mds.py:299: FutureWarning:

The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.



  Calculated metric MDS in 39.66 seconds.
Calculated PHATE in 46.35 seconds.
Calculating PHATE...
  Running PHATE on 3200 observations and 3 variables.
  Calculating graph and diffusion operator...
    Calculating KNN search...
    Calculated KNN search in 0.03 seconds.
    Calculating affinities...
    Calculated affinities in 0.02 seconds.
  Calculated graph and diffusion operator in 0.05 seconds.
  Calculating landmark operator...
    Calculating SVD...
    Calculated SVD in 0.14 seconds.
    Calculating KMeans...
    Calculated KMeans in 4.75 seconds.
  Calculated landmark operator in 5.68 seconds.
  Calculating diffusion potential...
  Calculated diffusion potential in 1.20 seconds.
  Calculating metric MDS...


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/sklearn/manifold/_mds.py:299: FutureWarning:

The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.



  Calculated metric MDS in 41.72 seconds.
Calculated PHATE in 48.66 seconds.


In [15]:
scatter(data_dict0['phate'], s=5)

In [17]:
data_dict1 = convert_data(X, knn=10, t=60)
scatter(data_dict1['phate'], s=5)

Calculating PHATE...
  Running PHATE on 4000 observations and 3 variables.
  Calculating graph and diffusion operator...
    Calculating KNN search...
    Calculated KNN search in 0.08 seconds.
    Calculating affinities...
    Calculated affinities in 0.03 seconds.
  Calculated graph and diffusion operator in 0.13 seconds.
  Calculating landmark operator...
    Calculating SVD...
    Calculated SVD in 0.30 seconds.
    Calculating KMeans...
    Calculated KMeans in 4.52 seconds.
  Calculated landmark operator in 5.79 seconds.
  Calculating diffusion potential...
  Calculated diffusion potential in 2.16 seconds.
  Calculating metric MDS...


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/sklearn/manifold/_mds.py:299: FutureWarning:

The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.



  Calculated metric MDS in 8.93 seconds.
Calculated PHATE in 17.03 seconds.
Calculating PHATE...
  Running PHATE on 3200 observations and 3 variables.
  Calculating graph and diffusion operator...
    Calculating KNN search...
    Calculated KNN search in 0.04 seconds.
    Calculating affinities...
    Calculated affinities in 0.02 seconds.
  Calculated graph and diffusion operator in 0.07 seconds.
  Calculating landmark operator...
    Calculating SVD...
    Calculated SVD in 0.15 seconds.
    Calculating KMeans...
    Calculated KMeans in 2.78 seconds.
  Calculated landmark operator in 3.51 seconds.
  Calculating diffusion potential...
  Calculated diffusion potential in 2.80 seconds.
  Calculating metric MDS...


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/sklearn/manifold/_mds.py:299: FutureWarning:

The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.



  Calculated metric MDS in 11.72 seconds.
Calculated PHATE in 18.11 seconds.


In [18]:
data_dict2 = convert_data(X, knn=20, t=60)
scatter(data_dict2['phate'], s=5)

Calculating PHATE...
  Running PHATE on 4000 observations and 3 variables.
  Calculating graph and diffusion operator...
    Calculating KNN search...
    Calculated KNN search in 0.15 seconds.
    Calculating affinities...
    Calculated affinities in 0.04 seconds.
  Calculated graph and diffusion operator in 0.20 seconds.
  Calculating landmark operator...
    Calculating SVD...
    Calculated SVD in 0.22 seconds.
    Calculating KMeans...
    Calculated KMeans in 6.29 seconds.
  Calculated landmark operator in 7.11 seconds.
  Calculating diffusion potential...
  Calculated diffusion potential in 2.28 seconds.
  Calculating metric MDS...


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/sklearn/manifold/_mds.py:299: FutureWarning:

The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.



  Calculated metric MDS in 22.15 seconds.
Calculated PHATE in 31.75 seconds.
Calculating PHATE...
  Running PHATE on 3200 observations and 3 variables.
  Calculating graph and diffusion operator...
    Calculating KNN search...
    Calculated KNN search in 0.07 seconds.
    Calculating affinities...
    Calculated affinities in 0.04 seconds.
  Calculated graph and diffusion operator in 0.11 seconds.
  Calculating landmark operator...
    Calculating SVD...
    Calculated SVD in 0.27 seconds.
    Calculating KMeans...
    Calculated KMeans in 3.14 seconds.
  Calculated landmark operator in 4.72 seconds.
  Calculating diffusion potential...
  Calculated diffusion potential in 2.15 seconds.
  Calculating metric MDS...


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/sklearn/manifold/_mds.py:299: FutureWarning:

The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.



  Calculated metric MDS in 18.22 seconds.
Calculated PHATE in 25.20 seconds.


In [8]:
data_dict2 = convert_data(X, knn=20, t=100)
scatter(data_dict2['phate'], s=5)

Calculating PHATE...
  Running PHATE on 4000 observations and 3 variables.
  Calculating graph and diffusion operator...
    Calculating KNN search...
    Calculated KNN search in 0.17 seconds.
    Calculating affinities...
    Calculated affinities in 0.04 seconds.
  Calculated graph and diffusion operator in 0.22 seconds.
  Calculating landmark operator...
    Calculating SVD...
    Calculated SVD in 0.22 seconds.
    Calculating KMeans...
    Calculated KMeans in 5.16 seconds.
  Calculated landmark operator in 6.31 seconds.
  Calculating diffusion potential...
  Calculated diffusion potential in 2.51 seconds.
  Calculating metric MDS...


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/sklearn/manifold/_mds.py:299: FutureWarning:

The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.



  Calculated metric MDS in 19.97 seconds.
Calculated PHATE in 29.03 seconds.
Calculating PHATE...
  Running PHATE on 3200 observations and 3 variables.
  Calculating graph and diffusion operator...
    Calculating KNN search...
    Calculated KNN search in 0.07 seconds.
    Calculating affinities...
    Calculated affinities in 0.04 seconds.
  Calculated graph and diffusion operator in 0.11 seconds.
  Calculating landmark operator...
    Calculating SVD...
    Calculated SVD in 0.17 seconds.
    Calculating KMeans...
    Calculated KMeans in 3.76 seconds.
  Calculated landmark operator in 4.97 seconds.
  Calculating diffusion potential...
  Calculated diffusion potential in 1.54 seconds.
  Calculating metric MDS...


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/sklearn/manifold/_mds.py:299: FutureWarning:

The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.



  Calculated metric MDS in 19.51 seconds.
Calculated PHATE in 26.14 seconds.


In [23]:
data_dict2 = convert_data(X, knn=20, t=100, decay=20)
scatter(data_dict2['phate'], s=5)

Calculating PHATE...
  Running PHATE on 4000 observations and 3 variables.
  Calculating graph and diffusion operator...
    Calculating KNN search...
    Calculated KNN search in 0.09 seconds.
    Calculating affinities...
    Calculated affinities in 0.04 seconds.
  Calculated graph and diffusion operator in 0.14 seconds.
  Calculating landmark operator...
    Calculating SVD...
    Calculated SVD in 0.22 seconds.
    Calculating KMeans...
    Calculated KMeans in 5.18 seconds.
  Calculated landmark operator in 6.01 seconds.
  Calculating diffusion potential...
  Calculated diffusion potential in 2.29 seconds.
  Calculating metric MDS...


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/sklearn/manifold/_mds.py:299: FutureWarning:

The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.



  Calculated metric MDS in 19.47 seconds.
Calculated PHATE in 27.93 seconds.
Calculating PHATE...
  Running PHATE on 3200 observations and 3 variables.
  Calculating graph and diffusion operator...
    Calculating KNN search...
    Calculated KNN search in 0.07 seconds.
    Calculating affinities...
    Calculated affinities in 0.04 seconds.
  Calculated graph and diffusion operator in 0.12 seconds.
  Calculating landmark operator...
    Calculating SVD...
    Calculated SVD in 0.18 seconds.
    Calculating KMeans...
    Calculated KMeans in 3.04 seconds.
  Calculated landmark operator in 3.80 seconds.
  Calculating diffusion potential...
  Calculated diffusion potential in 2.46 seconds.
  Calculating metric MDS...


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/sklearn/manifold/_mds.py:299: FutureWarning:

The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.



  Calculated metric MDS in 21.50 seconds.
Calculated PHATE in 27.91 seconds.


In [24]:
data_dict2 = convert_data(X, knn=20, t=100, decay=80)
scatter(data_dict2['phate'], s=5)

Calculating PHATE...
  Running PHATE on 4000 observations and 3 variables.
  Calculating graph and diffusion operator...
    Calculating KNN search...
    Calculated KNN search in 0.09 seconds.
    Calculating affinities...
    Calculated affinities in 0.04 seconds.
  Calculated graph and diffusion operator in 0.14 seconds.
  Calculating landmark operator...
    Calculating SVD...
    Calculated SVD in 0.21 seconds.
    Calculating KMeans...
    Calculated KMeans in 3.89 seconds.
  Calculated landmark operator in 4.92 seconds.
  Calculating diffusion potential...
  Calculated diffusion potential in 2.97 seconds.
  Calculating metric MDS...


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/sklearn/manifold/_mds.py:299: FutureWarning:

The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.



  Calculated metric MDS in 17.93 seconds.
Calculated PHATE in 25.98 seconds.
Calculating PHATE...
  Running PHATE on 3200 observations and 3 variables.
  Calculating graph and diffusion operator...
    Calculating KNN search...
    Calculated KNN search in 0.07 seconds.
    Calculating affinities...
    Calculated affinities in 0.04 seconds.
  Calculated graph and diffusion operator in 0.12 seconds.
  Calculating landmark operator...
    Calculating SVD...
    Calculated SVD in 0.17 seconds.
    Calculating KMeans...
    Calculated KMeans in 3.53 seconds.
  Calculated landmark operator in 4.61 seconds.
  Calculating diffusion potential...
  Calculated diffusion potential in 2.19 seconds.
  Calculating metric MDS...


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/sklearn/manifold/_mds.py:299: FutureWarning:

The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.



  Calculated metric MDS in 20.13 seconds.
Calculated PHATE in 27.06 seconds.


In [19]:
data_dict2 = convert_data(X, knn=20, t=200)
scatter(data_dict2['phate'], s=5)

Calculating PHATE...
  Running PHATE on 4000 observations and 3 variables.
  Calculating graph and diffusion operator...
    Calculating KNN search...
    Calculated KNN search in 0.26 seconds.
    Calculating affinities...
    Calculated affinities in 0.24 seconds.
  Calculated graph and diffusion operator in 0.53 seconds.
  Calculating landmark operator...
    Calculating SVD...
    Calculated SVD in 0.66 seconds.
    Calculating KMeans...
    Calculated KMeans in 5.73 seconds.
  Calculated landmark operator in 8.18 seconds.
  Calculating diffusion potential...
  Calculated diffusion potential in 2.70 seconds.
  Calculating metric MDS...


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/sklearn/manifold/_mds.py:299: FutureWarning:

The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.



  Calculated metric MDS in 23.89 seconds.
Calculated PHATE in 35.38 seconds.
Calculating PHATE...
  Running PHATE on 3200 observations and 3 variables.
  Calculating graph and diffusion operator...
    Calculating KNN search...
    Calculated KNN search in 0.07 seconds.
    Calculating affinities...
    Calculated affinities in 0.04 seconds.
  Calculated graph and diffusion operator in 0.13 seconds.
  Calculating landmark operator...
    Calculating SVD...
    Calculated SVD in 0.35 seconds.
    Calculating KMeans...
    Calculated KMeans in 3.48 seconds.
  Calculated landmark operator in 4.54 seconds.
  Calculating diffusion potential...
  Calculated diffusion potential in 2.58 seconds.
  Calculating metric MDS...


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/sklearn/manifold/_mds.py:299: FutureWarning:

The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.



  Calculated metric MDS in 21.04 seconds.
Calculated PHATE in 28.31 seconds.


In [12]:
data_dict4 = convert_data(X, knn=30, t=100)
scatter(data_dict3['phate'], s=5)

Calculating PHATE...
  Running PHATE on 4000 observations and 3 variables.
  Calculating graph and diffusion operator...
    Calculating KNN search...
    Calculated KNN search in 0.86 seconds.
    Calculating affinities...
    Calculated affinities in 0.25 seconds.
  Calculated graph and diffusion operator in 1.12 seconds.
  Calculating landmark operator...
    Calculating SVD...
    Calculated SVD in 0.31 seconds.
    Calculating KMeans...
    Calculated KMeans in 6.24 seconds.
  Calculated landmark operator in 7.27 seconds.
  Calculating diffusion potential...
  Calculated diffusion potential in 2.30 seconds.
  Calculating metric MDS...


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/sklearn/manifold/_mds.py:299: FutureWarning:

The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.



  Calculated metric MDS in 22.26 seconds.
Calculated PHATE in 33.02 seconds.
Calculating PHATE...
  Running PHATE on 3200 observations and 3 variables.
  Calculating graph and diffusion operator...
    Calculating KNN search...
    Calculated KNN search in 0.10 seconds.
    Calculating affinities...
    Calculated affinities in 0.05 seconds.
  Calculated graph and diffusion operator in 0.15 seconds.
  Calculating landmark operator...
    Calculating SVD...
    Calculated SVD in 0.20 seconds.
    Calculating KMeans...
    Calculated KMeans in 3.35 seconds.
  Calculated landmark operator in 4.76 seconds.
  Calculating diffusion potential...
  Calculated diffusion potential in 2.40 seconds.
  Calculating metric MDS...


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/sklearn/manifold/_mds.py:299: FutureWarning:

The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.



  Calculated metric MDS in 18.78 seconds.
Calculated PHATE in 26.10 seconds.


In [9]:
data_dict3 = convert_data(X, knn=40, t=100)
scatter(data_dict3['phate'], s=5)

Calculating PHATE...
  Running PHATE on 4000 observations and 3 variables.
  Calculating graph and diffusion operator...
    Calculating KNN search...
    Calculated KNN search in 0.16 seconds.
    Calculating affinities...
    Calculated affinities in 0.08 seconds.
  Calculated graph and diffusion operator in 0.25 seconds.
  Calculating landmark operator...
    Calculating SVD...
    Calculated SVD in 0.29 seconds.
    Calculating KMeans...
    Calculated KMeans in 4.02 seconds.
  Calculated landmark operator in 6.40 seconds.
  Calculating diffusion potential...
  Calculated diffusion potential in 2.18 seconds.
  Calculating metric MDS...


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/sklearn/manifold/_mds.py:299: FutureWarning:

The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.



  Calculated metric MDS in 18.96 seconds.
Calculated PHATE in 27.81 seconds.
Calculating PHATE...
  Running PHATE on 3200 observations and 3 variables.
  Calculating graph and diffusion operator...
    Calculating KNN search...
    Calculated KNN search in 0.12 seconds.
    Calculating affinities...
    Calculated affinities in 0.06 seconds.
  Calculated graph and diffusion operator in 0.20 seconds.
  Calculating landmark operator...
    Calculating SVD...
    Calculated SVD in 0.23 seconds.
    Calculating KMeans...
    Calculated KMeans in 4.36 seconds.
  Calculated landmark operator in 5.19 seconds.
  Calculating diffusion potential...
  Calculated diffusion potential in 2.33 seconds.
  Calculating metric MDS...


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/sklearn/manifold/_mds.py:299: FutureWarning:

The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.



  Calculated metric MDS in 21.31 seconds.
Calculated PHATE in 29.04 seconds.


In [13]:
data_dict5 = convert_data(X, knn=40, t=50)
scatter(data_dict5['phate'], s=5)

Calculating PHATE...
  Running PHATE on 4000 observations and 3 variables.
  Calculating graph and diffusion operator...
    Calculating KNN search...
    Calculated KNN search in 0.17 seconds.
    Calculating affinities...
    Calculated affinities in 0.08 seconds.
  Calculated graph and diffusion operator in 0.26 seconds.
  Calculating landmark operator...
    Calculating SVD...
    Calculated SVD in 0.28 seconds.
    Calculating KMeans...
    Calculated KMeans in 3.97 seconds.
  Calculated landmark operator in 5.30 seconds.
  Calculating diffusion potential...
  Calculated diffusion potential in 2.43 seconds.
  Calculating metric MDS...


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/sklearn/manifold/_mds.py:299: FutureWarning:

The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.



  Calculated metric MDS in 19.67 seconds.
Calculated PHATE in 27.67 seconds.
Calculating PHATE...
  Running PHATE on 3200 observations and 3 variables.
  Calculating graph and diffusion operator...
    Calculating KNN search...
    Calculated KNN search in 0.13 seconds.
    Calculating affinities...
    Calculated affinities in 0.06 seconds.
  Calculated graph and diffusion operator in 0.20 seconds.
  Calculating landmark operator...
    Calculating SVD...
    Calculated SVD in 0.23 seconds.
    Calculating KMeans...
    Calculated KMeans in 3.62 seconds.
  Calculated landmark operator in 4.52 seconds.
  Calculating diffusion potential...
  Calculated diffusion potential in 2.13 seconds.
  Calculating metric MDS...


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/sklearn/manifold/_mds.py:299: FutureWarning:

The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.



  Calculated metric MDS in 14.48 seconds.
Calculated PHATE in 21.35 seconds.


In [10]:
scatter(data_dict0['data'], s=5)

In [11]:
assert False
data_name = 'swiss_roll_wider'
np.savez(f"../../data/{data_name}.npz", **data_dict0)

AssertionError: 

In [ ]:
seed = 32
data_name = 'swiss_roll_wider'
noise_types = ['hi-freq-no-add']
noise_type = 'hi-freq-no-add'
noise_level = 1.
mask_dist = False
data_dict = add_negative_samples(data_dict0.copy(), subset_rate=1., noise_rate=noise_level, seed=seed, noise=noise_type, mask_dists=mask_dist, shell=True)
save_folder = f'../../data/negative_sampling_toy_shell/{mask_dist}/'
pathlib.Path(save_folder).mkdir(parents=True, exist_ok=True)
np.savez(f"{save_folder}/{data_name}.npz", **data_dict)
scatter(data_dict['data'], data_dict['mask_x'], s=2)